In [ ]:
# System_seed table info
dbutils.widgets.text("System_Id", "")
dbutils.widgets.text("tb_system_seed", "")

# Container Mounting credentials and info
dbutils.widgets.text("storage_account_name", "")
dbutils.widgets.text("storage_account_access_key", "")

In [1]:
# System_seed table info
System_Id = int(dbutils.widgets.get("System_Id"))
tb_system_seed = dbutils.widgets.get("tb_system_seed")

# Container Mounting credentials and info
storage_account_name = dbutils.widgets.get("storage_account_name")
storage_account_access_key = dbutils.widgets.get("storage_account_access_key")

print(System_Id)
print(storage_account_name)
print(storage_account_access_key)
print(tb_system_seed)

NameError: name 'dbutils' is not defined

In [ ]:
from pyspark.sql import SparkSession
from pyspark.sql.utils import AnalysisException
from datetime import datetime
from pyspark.sql.functions import col
from pyspark.sql.functions import col, upper

system_id = System_Id
records_read=0
record_inserted=0
df=""
trigged_by = dbutils.notebook.entry_point.getDbutils().notebook().getContext().userName().get()

In [ ]:
spark = SparkSession.builder.getOrCreate()

try:
    # Execute the Spark SQL query
    file_info = spark.sql("""
        SELECT *
        FROM {}
        WHERE System_Id = {}
    """.format(tb_system_seed, System_Id)).first()

    if file_info is None:
        raise ValueError("File details not found in system_seed table for system_id = {}".format(System_Id))

    source_db_container_name = file_info.Source_DB
    source_object_name = file_info.Source_Object_Name
    target_db = file_info.Target_DB
    target_object_name = file_info.Target_Object_Name
    source_Type = file_info.Source_Type	
    target_Type = file_info.Target_Type
    isDelta = file_info.IsDelta
    delta_Field = file_info.Delta_Field

    print(source_db_container_name)
    print(source_object_name)
    print(target_db)
    print(target_object_name)
    print(isDelta)
    print(delta_Field)
    print(source_Type)
except (AnalysisException, ValueError, Exception) as error:
    print("Error occurred while processing system_seed input:")
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception": str(error),"system_id":system_id}
    dbutils.notebook.exit(my_json)

integrated
account_table_details
curated
account_table_details
True
id
delta


In [ ]:
def source_mount(source_db_container_name,storage_account_name,storage_account_access_key):
    dbutils.fs.mount(
        source=f"wasbs://{source_db_container_name}@{storage_account_name}.blob.core.windows.net",
        mount_point=f"/mnt/{source_db_container_name}",
        extra_configs={
            f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_access_key
        },
    )
    print("Mount successful!")
try:
    source_mount(source_db_container_name,storage_account_name,storage_account_access_key)
except Exception as e:
    print(f"Already mounted {str(e).partition('is:')[0]}")

Already mounted An error occurred while calling o4400.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/integrated; nested exception 


In [ ]:
def source_mount(target_db,storage_account_name,storage_account_access_key):
    dbutils.fs.mount(
        source=f"wasbs://{target_db}@{storage_account_name}.blob.core.windows.net",
        mount_point=f"/mnt/{target_db}",
        extra_configs={
            f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_access_key
        },
    )
    print("Mount successful!")
try:
    source_mount(target_db,storage_account_name,storage_account_access_key)
except Exception as e:
    print(f"Already mounted {str(e).partition('is:')[0]}")

Already mounted An error occurred while calling o4400.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/curated; nested exception 


In [ ]:
def read_delta_file(source_db_container_name, source_object_name):
    if source_Type == "csv":
        print("csv")
        path = f"dbfs:/mnt/{source_db_container_name}/{source_object_name}.{source_Type}"
    else:
        print("delta")
        path = f"dbfs:/mnt/{source_db_container_name}/{source_object_name}"
        
    df = spark.read.format(source_Type).option("header", "true").option("inferSchema", "true").load(path)

    display(df.count())
    display(df)
    return df
try:
    df = read_delta_file(source_db_container_name, source_object_name)
    records_read=df.count()
except Exception as exp:
    exp=str(exp)
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
    dbutils.notebook.exit(my_json)

delta
30

id Member ID Snapshot Date Social Security Access Number Primary Owner Access Number Partition Key Birth Date Last Contact Date Last Activity Date Original MBRP Date Credit Date Last Update Date DBR Run ID Full Name First Name Middle Name Last Name Prefix Name Suffix Name Eighteen Plus Indicator Party Status Code Party type Membership Type Code Business Membership Flag Membership Flag Create Date Member init open date Member last activity Date Gender Code Primary language type code Employment Status Code Designation Salary Military Brach Code/Military service code Military Rank Code Origin Code/Membership Origin Type code 045848162922 679620458 06-11-2023 611-17-4816 6938232922 4598695544 6 5/19/1948 6/25/2023 3/25/2023 1/28/2023 05-07-2023 2/17/2023 33869 Stephanie Hill Gabrielle Eric Robinson Miss III FALSE A Individual Silver TRUE TRUE 08-12-2022 01-11-2023 6/18/2023 M Spanish Unemployed Petroleum engineer 57509 Navy Corporal In-person 404992201864 706684049 5/13/2023 475-12-9220 9263881864 9821422479 10 04-05-1980 4/16/2023 01-11-2023 10/20/2022 11-04-2022 10-10-2022 50783 Alyssa Smith Courtney Madison Johnson Mx. MD FALSE C Individual Gold TRUE TRUE 5/26/2023 01-05-2023 06-03-2023 F English Unemployed Theme park manager 473439 Army Private In-person 858349941829 315608583 5/14/2023 467-86-4994 8504911829 495623827 5 5/29/1976 6/25/2023 12/15/2022 11-01-2022 09-08-2022 08-10-2022 4734 Eric Soto Lisa John Reese Dr. Jr. FALSE B Organization Bronze TRUE TRUE 8/13/2022 02-06-2023 1/19/2023 F French Unemployed Patent examiner 919531 Navy Corporal Online 924631312246 118419246 12-01-2022 158-38-3131 3466092246 6380003913 3 11-03-1982 12-07-2022 05-11-2023 9/21/2022 11/19/2022 1/17/2023 29584 Brian Thornton Kimberly Ernest Jenkins Mx. DVM TRUE C Organization Bronze FALSE FALSE 6/23/2023 03-07-2023 6/22/2023 M French Employed Educational psychologist 727340 Army Private Online 821882047286 167138218 10/27/2022 278-66-8204 3111327286 2119644185 3 11/30/1934 03-04-2023 8/22/2022 11/15/2022 1/27/2023 03-05-2023 61424 Michael Larson Claire Dana Williams Dr. MD FALSE C Organization Silver FALSE FALSE 3/26/2023 12-05-2022 07-12-2022 F Spanish Employed Tour manager 345931 Air Force Private Referral 071814647126 226610718 8/23/2022 235-53-1464 9127847126 2209712458 6 10/19/1935 12-03-2022 05-01-2023 6/30/2023 12/19/2022 04-06-2023 15009 Andrew Strong Laura Jonathon Kelly Mx. DVM TRUE C Organization Bronze FALSE TRUE 10-05-2022 6/25/2023 03-04-2023 M French Employed Financial manager 89440 Air Force Private Online 804023007438 449478040 5/30/2023 410-27-2300 4051667438 7546523439 10 12/15/1964 8/28/2022 08-04-2022 12/13/2022 08-02-2022 9/17/2022 33189 Kurt Ellis Reginald Kristina Berg Dr. DDS FALSE A Organization Bronze TRUE FALSE 03-04-2023 11/15/2022 07-06-2022 M French Employed Regulatory affairs officer 956513 Navy Corporal Referral 368621608458 378613686 10/22/2022 148-95-2160 8776528458 8001806529 1 8/29/1958 10-09-2022 6/23/2023 3/25/2023 9/29/2022 4/27/2023 12561 Amanda Parker Brandon Cheryl Keller Dr. Jr. FALSE B Individual Gold FALSE TRUE 12-07-2022 12/18/2022 2/19/2023 F English Employed Naval architect 241767 Navy Private Referral 047699239995 916880476 08-02-2022 169-09-9923 4657659995 5556425040 1 8/29/1940 11/20/2022 7/16/2022 7/28/2022 5/17/2023 4/28/2023 76090 Corey Ray Kendra Mary Johnson Dr. MD TRUE A Individual Gold FALSE TRUE 9/18/2022 11-02-2022 8/19/2022 M French Unemployed Comptroller 336914 Navy Sergeant Online 911522191843 191839115 10/18/2022 220-90-2219 5359681843 884046611 4 4/16/1962 04-01-2023 11-03-2022 2/19/2023 10/14/2022 12-09-2022 63979 Michael Serrano Cynthia John Jones Mrs. DDS TRUE A Organization Gold FALSE FALSE 12/20/2022 05-08-2023 07-05-2023 F English Unemployed Agricultural engineer 490145 Air Force Sergeant Referral 653894658980 641106538 6/27/2023 672-47-9465 2930608980 2449972963 3 1/15/1953 8/21/2022 02-12-2023 5/19/2023 01-12-2023 8/31/2022 37784 Nicole Logan Brandon Gerald Fischer Mr. MD FA

In [ ]:
# from pyspark.sql import SparkSession
# from pyspark.sql.functions import concat_ws, substring, struct,StringType

# def create_id_column(row):
#     # Extract the last four digits from each column and concatenate them to form the 'id'
#     return f"{row['Member ID'][-4:]}{row['Social Security'][-4:]}{row['Access Number'][-4:]}"

# create_id_udf = udf(create_id_column, StringType())
# df_with_id = df.withColumn('id', create_id_udf(struct([df[col] for col in ['Member ID', 'Social Security', 'Access Number']])))

# display(df_with_id)

In [ ]:
from pyspark.sql.functions import col
duplicates_df = df.groupBy("id").count().where(col("count") > 1)
display(duplicates_df)

id count

In [ ]:
def check_path_exists(path):
    try:
        file_list = dbutils.fs.ls(path)
        return True
    except Exception as e:
        return False

In [ ]:
from pyspark.sql import SparkSession
from delta.tables import DeltaTable

def get_record_inserted():
    path = f"dbfs:/mnt/{target_db}/{target_object_name}"
    
    try:
        spark = SparkSession.builder.appName("Get Record Inserted").getOrCreate()
        delta_table_updates = DeltaTable.forPath(spark, path)
        history_df = delta_table_updates.history()
        history_df.createOrReplaceTempView("delta_history")
        query = "SELECT * FROM delta_history ORDER BY version DESC LIMIT 1"
        latest_history = spark.sql(query)
        operation = latest_history.collect()[0].operation
        if operation == "WRITE":
            record_inserted = int(latest_history.collect()[0].operationMetrics["numOutputRows"])
        else:
            record_inserted = int(latest_history.collect()[0].operationMetrics["numTargetRowsInserted"])
        return record_inserted
    except Exception as e:
        print("An error occurred while getting record inserted:", e)
        return None

In [ ]:
def insert_data(data, path):
    spark.conf.set('spark.databricks.delta.schema.autoMerge.enabled',True)
    spark.conf.set("spark.databricks.delta.properties.defaults.columnMapping.mode","name")
    data.write.option("header","true").format("delta").option("overwriteSchema", "true").option("delta.columnMapping.mode", "name").mode('append').save(path)

# try:
#     path = f"dbfs:/mnt/{target_db}/{target_object_name}"
#     insert_data(df, path)
#     # record_inserted = get_record_inserted()
# except Exception as exp:
#     exp=str(exp)
#     my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
#     dbutils.notebook.exit(my_json)
# print(record_inserted)

In [ ]:
from delta.tables import *

def incremental_load(path,sourceDF):
    targetDF = DeltaTable.forPath(spark, path)
    
    spark.conf.set('spark.databricks.delta.schema.autoMerge.enabled',True)
    targetDF.alias('target') \
    .merge(
        sourceDF.alias('source'),
        'target.id = source.id'
    ) \
    .whenMatchedUpdateAll() \
    .whenNotMatchedInsertAll()\
    .execute()

In [ ]:
try:
    outputpath=f"dbfs:/mnt/{target_db}/{target_object_name}"
    if (isDelta == True):
        if (check_path_exists(outputpath)):
            print("exist")
            incremental_load(outputpath,df)
        else:
            print("doesnt exist")
            insert_data(df,outputpath)
    else:
        insert_data(df,outputpath)
except Exception as e:
    print(e)
    exp=str(e)
    if("PATH_NOT_FOUND" in exp):
         insert_data(df,outputpath)
    else:
        my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
        dbutils.notebook.exit(my_json)

exist


In [ ]:
def read_curated_file(target_db, target_object_name):
    path = f"dbfs:/mnt/{target_db}/{target_object_name}"
    df = spark.read.format(target_Type).option("header", "true").load(path)
    display(df)
    display(df.count())
try:
    read_curated_file(target_db, target_object_name)
except Exception as exp:
    exp=str(exp)
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
    dbutils.notebook.exit(my_json)

id Member ID Snapshot Date Social Security Access Number Primary Owner Access Number Partition Key Birth Date Last Contact Date Last Activity Date Original MBRP Date Credit Date Last Update Date DBR Run ID Full Name First Name Middle Name Last Name Prefix Name Suffix Name Eighteen Plus Indicator Party Status Code Party type Membership Type Code Business Membership Flag Membership Flag Create Date Member init open date Member last activity Date Gender Code Primary language type code Employment Status Code Designation Salary Military Brach Code/Military service code Military Rank Code Origin Code/Membership Origin Type code test 637594212713 101076375 21-12-2023 652-02-9421 3678842713 4214717945 6 8/25/1990 12/20/2022 11-07-2022 06-02-2023 03-10-2023 1/27/2023 21993 Caroline Lane Jenna Ronald Williams Mr. MD FALSE A Individual Silver FALSE TRUE 4/29/2023 9/24/2022 08-10-2022 F Spanish Employed Occupational hygienist 990433 Air Force Corporal Referral null 556366084287 867065563 10/23/2022 246-44-6608 8269324287 1681754655 1 4/21/1980 10/20/2022 07-02-2023 12/27/2022 04-06-2023 6/18/2023 9828 Stephanie Hinton Paul Randy Lewis Mr. MD FALSE A Organization Silver FALSE TRUE 9/27/2022 07-04-2023 07-10-2022 F Spanish Unemployed Barrister 292151 Navy Corporal In-person null 857896472068 773628578 4/18/2023 168-04-9647 6408002068 2712099696 4 12/23/1988 12/26/2022 4/17/2023 1/14/2023 6/28/2023 03-01-2023 86452 Gabriel Carter Jennifer Dan Whitehead Mrs. Jr. TRUE A Organization Silver TRUE TRUE 7/17/2022 6/21/2023 4/26/2023 F French Employed Teacher, early years/pre 315641 Army Corporal Referral null 640705089623 226816407 6/14/2023 347-90-0508 3132129623 5874532223 7 11-07-2001 12-07-2022 2/26/2023 10/15/2022 1/19/2023 12/19/2022 13566 Brittany Sanders Kathleen James Hoover Ms. DDS TRUE A Individual Bronze FALSE FALSE 10/25/2022 8/13/2022 4/13/2023 F Spanish Employed Aid worker 843900 Air Force Sergeant In-person null 377794062133 205513777 6/27/2023 727-31-9406 7792512133 6222536514 8 02-03-2001 2/19/2023 2/19/2023 7/14/2022 01-01-2023 9/26/2022 82649 Pamela Sanders William Andrew Yang Misc. IV TRUE B Organization Silver TRUE TRUE 11/21/2022 07-09-2022 3/20/2023 M Spanish Employed Prison officer 682152 Army Sergeant Online null 843876207923 104418438 12/27/2022 576-33-7620 569277923 1853291463 3 7/18/1991 09-12-2022 5/19/2023 10-09-2022 1/20/2023 8/30/2022 70303 Thomas Thomas April Angela Gutierrez Mr. MD FALSE C Organization Bronze FALSE TRUE 4/19/2023 08-12-2022 09-11-2022 F English Employed Psychologist, educational 55994 Air Force Sergeant Online null 382214121326 261073822 4/15/2023 733-12-1412 7048221326 4673091614 9 08-11-1979 12/27/2022 7/26/2022 10-07-2022 7/19/2022 03-11-2023 24885 Tammy Gordon Anthony Nicholas Wilson Ms. Jr. TRUE A Individual Silver FALSE TRUE 8/30/2022 02-03-2023 5/13/2023 F English Employed Textile designer 411193 Navy Private Online null 596969735817 145705969 5/22/2023 502-37-6973 3058675817 1308763277 1 09-01-1988 5/21/2023 4/29/2023 7/18/2022 2/25/2023 3/30/2023 56088 Amber Berry Deborah Dustin Ballard Mrs. Jr. TRUE B Organization Gold TRUE FALSE 9/20/2022 8/31/2022 7/20/2022 M French Employed Youth worker 528805 Navy Private In-person null 350204356414 280783502 02-08-2023 675-47-0435 3407076414 6045471726 6 9/28/1947 12/27/2022 11-06-2022 11/30/2022 2/17/2023 03-12-2023 31855 Chelsea Beck John Andrea Johnson Mr. DDS FALSE A Individual Bronze FALSE FALSE 03-08-2023 6/16/2023 3/30/2023 M Spanish Unemployed Surveyor, minerals 68037 Air Force Corporal In-person null 049912530939 263120499 10/26/2022 609-82-1253 1433770939 8505549789 2 09-03-1985 3/24/2023 2/27/2023 11-02-2022 06-06-2023 8/31/2022 21518 Diana Estrada Nicole Julie Harris Ms. Jr. FALSE C Individual Bronze TRUE TRUE 8/25/2022 3/29/2023 11/26/2022 F English Unemployed Private music teacher 699328 Army Sergeant Referral null 527958662455 250975279 10-09-2022 616-94-5866 2511802455 44728276 4 5/18/1941 12/30/2022 11/29/2022 08-05-2022 3/13/2023 

6679

In [ ]:
my_json={"records_read":records_read,"record_inserted":get_record_inserted(),"trigged_by":trigged_by,"exception":'',"system_id":system_id}
dbutils.notebook.exit(my_json)